0. INSTALL dan download Docker

1. INSTALL mongo + cassandra di cmd + install pymongo Pake code dibawah di CMD

In [ ]:
#CMD
pip install pymongo
docker pull mongo
docker pull cassandra

2. Cari folder di file explorer untuk Buat directory, simpan PATHnya
contoh : D:\Kuliah\ROSBD\code
3. Buka CMDnya lalu masuk ke path tersebut
Jika path awal C: mau ke D:<br>
ketik





In [ ]:
D:
cd D:\Kuliah\ROSBD\code

# lanjut dibawah ini di CMD

mkdir my-database-project
cd my-database-project

4. Buat docker-compose.YML file buat config

In [ ]:
#CMD
echo. > docker-compose.yml

Isi docker-compose.yml

In [ ]:
version: '3.8'

services:
  mongodb:
    image: mongo:latest
    container_name: my-mongodb-instance
    ports:
      - "27017:27017"
    volumes:
      - mongodb_data:/data/db # Persist MongoDB data
    environment:
      MONGO_INITDB_ROOT_USERNAME: user # Optional: for basic authentication
      MONGO_INITDB_ROOT_PASSWORD: pass
    restart: always # Keep the container running

  cassandra:
    image: cassandra:latest
    container_name: my-cassandra-instance
    ports:
      - "9042:9042" # CQL port
      - "7000:7000" # Intra-node communication
    volumes:
      - cassandra_data:/var/lib/cassandra # Persist Cassandra data
    environment:
      CASSANDRA_CLUSTER_NAME: 'MyCassandraCluster' # Optional: cluster name
    restart: always # Keep the container running
    healthcheck: # Healthcheck to ensure Cassandra is ready
      test: ["CMD-SHELL", "[ $$(nodetool statusgossip) = \"RUNNING\" ] || exit 1"]
      interval: 30s
      timeout: 10s
      retries: 5

volumes:
  mongodb_data: # Define the named volume for MongoDB
  cassandra_data: # Define the named volume for Cassandra


5. Cek apakah mangodb dan cassandra sudah berjalan, hasil portnya di inget nanti dimasukkin di step- step selanjutnya

In [ ]:
#CMD
docker compose up -d
docker ps

## Mango DB


6. Import Movies di Python

In [ ]:
#Py
import csv
from pymongo import MongoClient

# --- Configuration for your MongoDB connection ---
# Replace with your Dockerized MongoDB host and port
# If you changed the host port, use that here (e.g., 27018)
MONGO_HOST = 'localhost'
MONGO_PORT = 27017 # This should be the host port you mapped in docker-compose.yml

DATABASE_NAME = 'moviedb_from_python' # This will be the name of your new database
COLLECTION_NAME = 'movies_collection' # This will be the name of your new collection

# --- CORRECTED CSV_FILE_PATH ---
# Use a raw string (r"...") for Windows paths to avoid issues with backslashes,
# or use forward slashes (which Python handles correctly on Windows too).
# Also, remove the extra double quotes around the path.
CSV_FILE_PATH = r"D:\Kuliah\ROSBD\ml-latest-small\movies.csv" #ini diganti tempat naruh dataset 1 yg movie

# --- MongoDB Authentication Credentials (from your docker-compose.yml) ---
MONGO_USERNAME = 'user' # As defined by MONGO_INITDB_ROOT_USERNAME
MONGO_PASSWORD = 'pass' # As defined by MONGO_INITDB_ROOT_PASSWORD
AUTH_SOURCE = 'admin'   # The database where the user is defined

# Initialize client outside try-except to ensure it's accessible in finally
client = None
db = None
collection = None

try:
    # --- Establish MongoDB Connection ---
    # Now including username, password, and authSource for authentication
    client = MongoClient(MONGO_HOST, MONGO_PORT, username=MONGO_USERNAME, password=MONGO_PASSWORD, authSource=AUTH_SOURCE)

    db = client[DATABASE_NAME]
    collection = db[COLLECTION_NAME]
    print(f"Successfully connected to MongoDB: {MONGO_HOST}:{MONGO_PORT}")
    print(f"Targeting database: '{DATABASE_NAME}', collection: '{COLLECTION_NAME}'")

    # --- Read CSV and Prepare Data for Insertion ---
    documents_to_insert = []
    try:
        with open(CSV_FILE_PATH, mode='r', encoding='utf-8') as file:
            csv_reader = csv.DictReader(file)
            # Each row will be a dictionary where keys are column headers
            for row in csv_reader:
                # --- Data Type Conversion (Important for numbers) ---
                # 'movies.csv' typically has 'movieId' as a number. Convert it.
                if 'movieId' in row and row['movieId']:
                    try:
                        row['movieId'] = int(row['movieId'])
                    except ValueError:
                        print(f"Warning: Failed to convert movieId '{row['movieId']}' to integer. Keeping as string.")
                
                # Add more type conversions here if other columns are numbers, booleans, etc.
                
                documents_to_insert.append(row)

        print(f"Read {len(documents_to_insert)} rows from '{CSV_FILE_PATH}'.")

    except FileNotFoundError:
        print(f"ERROR: The CSV file was not found at '{CSV_FILE_PATH}'.")
        print("Please ensure the 'movies.csv' file is in the same directory as this Python script,")
        print("or update the 'CSV_FILE_PATH' variable in the script with the correct full path.")
        # Re-raise or exit, depending on desired behavior
        exit()
    except Exception as e:
        print(f"An error occurred while reading the CSV file: {e}")
        exit()

    # --- Insert Data into MongoDB ---
    if documents_to_insert:
        try:
            # Insert all documents in one go (more efficient for large datasets)
            result = collection.insert_many(documents_to_insert)
            print(f"Successfully inserted {len(result.inserted_ids)} documents.")
        except Exception as e:
            print(f"ERROR: Failed to insert documents into MongoDB: {e}")
    else:
        print("No documents to insert (CSV was empty or had no valid data).")

except Exception as e:
    print(f"An unexpected error occurred during the overall process: {e}")

finally:
    # --- Ensure MongoDB Connection is Closed ---
    if client:
        client.close()
        print("MongoDB connection closed.")


Successfully connected to MongoDB: localhost:27017
Targeting database: 'moviedb_from_python', collection: 'movies_collection'
Read 9742 rows from 'D:\Kuliah\ROSBD\ml-latest-small\movies.csv'.
Successfully inserted 9742 documents.
MongoDB connection closed.


7. Cek apakah sudah konek dan masuk di DB Mango lewat CMD

In [ ]:
docker exec -it my-mongodb-instance mongosh -u user -p pass --authenticationDatabase admin
use moviedb_from_python
db.movies_collection.find().limit(5)
db.movies_collection.countDocuments()

#kalau sudah
exit

<details>
<summary><strong>📘 Daftar Lengkap Perintah MongoDB + Contoh (Klik untuk buka/tutup)</strong></summary>

---

## 🔹 1. Database Operations

| Command | Fungsi | Contoh |
|--------|--------|--------|
| `show dbs` | Menampilkan semua database | `show dbs` |
| `use <db_name>` | Berpindah atau membuat database | `use toko_online` |
| `db` | Menampilkan database aktif | `db` |
| `db.dropDatabase()` | Menghapus database aktif | `db.dropDatabase()` |

---

## 🔹 2. Collection Operations

| Command | Fungsi | Contoh |
|--------|--------|--------|
| `show collections` | Menampilkan semua koleksi dalam database | `show collections` |
| `db.createCollection("nama")` | Membuat koleksi baru | `db.createCollection("produk")` |
| `db.namaCollection.drop()` | Menghapus koleksi | `db.produk.drop()` |

---

## 🔹 3. Document Operations

| Command | Fungsi | Contoh |
|--------|--------|--------|
| `db.namaCollection.insertOne({...})` | Tambah satu dokumen | `db.user.insertOne({name: "Budi", age: 25})` |
| `db.namaCollection.insertMany([{...}, {...}])` | Tambah banyak dokumen | `db.user.insertMany([{name: "Ani"}, {name: "Dewi"}])` |
| `db.namaCollection.find()` | Menampilkan semua dokumen | `db.user.find()` |
| `db.namaCollection.findOne()` | Menampilkan satu dokumen | `db.user.findOne()` |
| `db.namaCollection.find({kriteria})` | Menampilkan dokumen berdasarkan filter | `db.user.find({age: {$gt: 20}})` |
| `db.namaCollection.updateOne({filter}, {$set: {...}})` | Update satu dokumen | `db.user.updateOne({name: "Budi"}, {$set: {age: 30}})` |
| `db.namaCollection.updateMany({filter}, {$set: {...}})` | Update banyak dokumen | `db.user.updateMany({}, {$set: {active: true}})` |
| `db.namaCollection.deleteOne({...})` | Hapus satu dokumen | `db.user.deleteOne({name: "Ani"})` |
| `db.namaCollection.deleteMany({...})` | Hapus banyak dokumen | `db.user.deleteMany({age: {$lt: 18}})` |

---

## 🔹 4. Indexing

| Command | Fungsi | Contoh |
|--------|--------|--------|
| `db.namaCollection.createIndex({field: 1})` | Membuat index menaik | `db.user.createIndex({name: 1})` |
| `db.namaCollection.getIndexes()` | Lihat semua index | `db.user.getIndexes()` |

---

## 🔹 5. Aggregation

### 📌 Contoh: Hitung total durasi ditonton per user
```js
db.watch_history.aggregate([
  { $group: { _id: "$user_id", total_duration: { $sum: "$duration_watched" } } }
])
```
---

### 📌 Contoh: Filter user dan hitung berapa film yang ditonton
```js
db.watch_history.aggregate([
  { $match: { user_id: "123" } },
  { $group: { _id: "$movie_id", total_watched: { $sum: 1 } } }
])
```
---

## 🔹 6. Statistik dan Admin

| Command | Fungsi | Contoh |
|--------|--------|--------|
| `db.stats` | Statistik database aktif | `db.stats()` |
| `db.namaCollection.stats()` | 	Statistik koleksi | `	db.user.stats()` |
| `db.serverStatus()` | 	Informasi server MongoDB	 | ` db.serverStatus()` |

---


In [ ]:
#nothing

## Cassandra

8. Buat DB di Cassandra via CMD
- Buat Keyspace (database di Cassandra)
- Buat Table watch_history

In [ ]:
docker exec -it my-cassandra-instance cqlsh
CREATE KEYSPACE watch_history_db
WITH replication = {'class': 'SimpleStrategy', 'replication_factor': 1};
USE watch_history_db;

CREATE TABLE watch_history (
    user_id text,
    movie_id text,
    watch_time timestamp,
    duration_watched int,
    PRIMARY KEY ((user_id, movie_id), watch_time)
);

9. Import file movie_db.watch_history.json di cassandra

In [17]:
import json
from cassandra.cluster import Cluster
# from cassandra.auth import PlainTextAuthProvider # Uncomment if Cassandra auth is enabled
from datetime import datetime

# --- Configuration ---
CASSANDRA_HOSTS = ['localhost'] # Your Docker host for Cassandra
CASSANDRA_PORT = 9042           # The host port mapped in docker-compose.yml

# --- CUSTOMIZE THESE TO MATCH YOUR CQL SCHEMA AND JSON FILE ---
KEYSPACE_NAME = 'watch_history_db'      # The Keyspace you created in cqlsh
TABLE_NAME = 'watch_history'            # The Table you created in cqlsh
JSON_FILE_PATH = r"D:\Kuliah\ROSBD\ml-latest-small\movie_db.watch_history.json" #ganti ke path dataset 2 yang watch history

# --- Authentication (if you enabled authentication for Cassandra) ---
# If your Cassandra has authentication enabled (not default in basic setup), uncomment and fill these:
# CASSANDRA_USERNAME = 'your_cassandra_username'
# CASSANDRA_PASSWORD = 'your_cassandra_password'

# Initialize cluster outside try-except for finally block
cluster = None
session = None

try:
    # --- Connect to Cassandra ---
    # If using authentication, uncomment and use auth_provider:
    # auth_provider = PlainTextAuthProvider(username=CASSANDRA_USERNAME, password=CASSANDRA_PASSWORD)
    # cluster = Cluster(CASSANDRA_HOSTS, port=CASSANDRA_PORT, auth_provider=auth_provider)
    
    cluster = Cluster(CASSANDRA_HOSTS, port=CASSANDRA_PORT) # For basic setup without auth
    
    session = cluster.connect(KEYSPACE_NAME)
    print(f"Connected to Cassandra cluster: {CASSANDRA_HOSTS}:{CASSANDRA_PORT}")
    print(f"Using Keyspace: '{KEYSPACE_NAME}'")

except Exception as e:
    print(f"ERROR: Could not connect to Cassandra. Please ensure your Docker container is running and ports are correct.")
    print(f"Details: {e}")
    exit()

# --- Read JSON Data ---
json_data = []
try:
    with open(JSON_FILE_PATH, 'r', encoding='utf-8') as f:
        json_data = json.load(f)
    print(f"Read {len(json_data)} records from '{JSON_FILE_PATH}'.")

except FileNotFoundError:
    print(f"ERROR: JSON file not found at '{JSON_FILE_PATH}'.")
    print("Please ensure the file exists and the path is correct in the script.")
    exit()
except json.JSONDecodeError as e:
    print(f"ERROR: Invalid JSON format in '{JSON_FILE_PATH}'. Details: {e}")
    print("Ensure the file contains valid JSON (e.g., a list of objects or a single object).")
    exit()
except Exception as e:
    print(f"An unexpected error occurred while reading the JSON file: {e}")
    exit()

# --- Prepare and Insert Data ---
# The order of columns in VALUES(...) must match the order of columns in the prepared statement.
insert_statement = session.prepare(
    f"INSERT INTO {TABLE_NAME} (user_id, movie_id, watch_time, duration_watched) VALUES (?, ?, ?, ?)"
)
try: 
    inserted_count = 0
    for record in json_data:
        try:
            # Extract and convert data based on your JSON structure
            user_id = record.get('user_id')
            movie_id = record.get('movie_id') # Stays text as it's quoted in JSON
            
            # Handle the "$date" object for watch_time
            watch_time_obj = record.get('watch_time')
            watch_time_str = watch_time_obj.get('$date') if watch_time_obj and '$date' in watch_time_obj else None
            
            if watch_time_str:
                # Convert ISO 8601 string to Python datetime object for Cassandra timestamp type
                watch_time = datetime.fromisoformat(watch_time_str.replace('Z', '+00:00')) # Handles 'Z' for UTC
            else:
                watch_time = None # Or handle as error if watch_time is mandatory

            duration_watched = int(record.get('duration_watched'))

            # Execute the insert statement with the extracted values
            session.execute(insert_statement, (user_id, movie_id, watch_time, duration_watched))
            inserted_count += 1
            print(f"Successfully inserted {inserted_count} records into Cassandra table '{TABLE_NAME}'.")
        except Exception as e:
            print(f"Warning: Failed to insert record: {record}. Error: {e}")


# --- Close Cassandra Connection ---
finally:
    if cluster: # Check if cluster object was successfully created
            cluster.shutdown()
            print("Cassandra connection closed.")

Connected to Cassandra cluster: ['localhost']:9042
Using Keyspace: 'watch_history_db'
Read 50000 records from 'D:\Kuliah\ROSBD\ml-latest-small\movie_db.watch_history.json'.
Successfully inserted 1 records into Cassandra table 'watch_history'.
Successfully inserted 2 records into Cassandra table 'watch_history'.
Successfully inserted 3 records into Cassandra table 'watch_history'.
Successfully inserted 4 records into Cassandra table 'watch_history'.
Successfully inserted 5 records into Cassandra table 'watch_history'.
Successfully inserted 6 records into Cassandra table 'watch_history'.
Successfully inserted 7 records into Cassandra table 'watch_history'.
Successfully inserted 8 records into Cassandra table 'watch_history'.
Successfully inserted 9 records into Cassandra table 'watch_history'.
Successfully inserted 10 records into Cassandra table 'watch_history'.
Successfully inserted 11 records into Cassandra table 'watch_history'.
Successfully inserted 12 records into Cassandra table '

<details>
<summary><strong>📘 Daftar Perintah Cassandra + Contoh (Klik untuk buka/tutup)</strong></summary>

---

## 🔹 1. Database & Keyspace Operations

| Perintah | Fungsi | Contoh |
|---------|--------|--------|
| `DESCRIBE KEYSPACES;` | Lihat semua keyspace | `DESCRIBE KEYSPACES;` |
| `CREATE KEYSPACE nama WITH replication = {...};` | Membuat keyspace | `CREATE KEYSPACE mykeyspace WITH replication = {'class':'SimpleStrategy', 'replication_factor':1};` |
| `USE nama_keyspace;` | Gunakan keyspace tertentu | `USE mykeyspace;` |
| `DROP KEYSPACE nama;` | Hapus keyspace | `DROP KEYSPACE mykeyspace;` |

---

## 🔹 2. Table Operations

| Perintah | Fungsi | Contoh |
|---------|--------|--------|
| `DESCRIBE TABLES;` | Lihat semua tabel dalam keyspace | `DESCRIBE TABLES;` |
| `CREATE TABLE nama (...);` | Membuat tabel | `CREATE TABLE users (id UUID PRIMARY KEY, name text, age int);` |
| `DROP TABLE nama;` | Menghapus tabel | `DROP TABLE users;` |
| `ALTER TABLE nama ADD kolom tipe;` | Menambah kolom | `ALTER TABLE users ADD email text;` |
| `TRUNCATE nama_tabel;` | Menghapus semua isi tabel tanpa menghapus strukturnya | `TRUNCATE users;` |

---

## 🔹 3. Insert & Select

| Perintah | Fungsi | Contoh |
|---------|--------|--------|
| `INSERT INTO ... VALUES (...);` | Menambahkan data | `INSERT INTO users (id, name, age) VALUES (uuid(), 'Budi', 30);` |
| `SELECT * FROM ...;` | Menampilkan seluruh data | `SELECT * FROM users;` |
| `SELECT kolom FROM ... WHERE ...;` | Menampilkan dengan kondisi | `SELECT name FROM users WHERE id = ...;` |
| `SELECT COUNT(*) FROM ...;` | Menghitung jumlah baris | `SELECT COUNT(*) FROM users;` |

---

## 🔹 4. Update & Delete

| Perintah | Fungsi | Contoh |
|---------|--------|--------|
| `UPDATE nama_tabel SET kolom=... WHERE pk=...;` | Update data | `UPDATE users SET age = 35 WHERE id = ...;` |
| `DELETE kolom FROM ... WHERE pk=...;` | Menghapus kolom | `DELETE email FROM users WHERE id = ...;` |
| `DELETE FROM ... WHERE pk=...;` | Hapus seluruh baris | `DELETE FROM users WHERE id = ...;` |

---

## 🔹 5. Clustering & Partition

| Perintah | Fungsi | Contoh |
|---------|--------|--------|
| `PRIMARY KEY (id)` | Partition key | `PRIMARY KEY (id)` |
| `PRIMARY KEY ((id), name)` | Partition + Clustering key | `PRIMARY KEY ((id), name)` |

---

## 🔹 6. Miscellaneous

| Perintah | Fungsi | Contoh |
|---------|--------|--------|
| `CONSISTENCY;` | Menampilkan tingkat konsistensi | `CONSISTENCY;` |
| `DESCRIBE nama_tabel;` | Detail struktur tabel | `DESCRIBE users;` |
| `EXIT;` | Keluar dari CQLSH | `EXIT;` |

---

### 📌 Contoh Nyata

```sql
-- Buat keyspace
CREATE KEYSPACE rosbd WITH replication = {'class': 'SimpleStrategy', 'replication_factor': 1};

-- Gunakan keyspace
USE rosbd;

-- Buat tabel
CREATE TABLE watch_history (
  user_id text,
  movie_id text,
  watch_time timestamp,
  duration_watched int,
  PRIMARY KEY (user_id, movie_id)
);

-- Tambahkan data
INSERT INTO watch_history (user_id, movie_id, watch_time, duration_watched)
VALUES ('u001', 'm123', toTimestamp(now()), 120);

-- Query data
SELECT * FROM watch_history;


In [ ]:
#nothing

## Query

In [22]:
import json
from pymongo import MongoClient
from cassandra.cluster import Cluster
from cassandra.auth import PlainTextAuthProvider # Uncomment if Cassandra auth is enabled
from datetime import datetime
from collections import defaultdict, Counter

# --- Configuration for MongoDB ---
MONGO_HOST = 'localhost'
MONGO_PORT = 27017 # Your MongoDB host port
MONGO_DB_NAME = 'moviedb_from_python'
MONGO_COLLECTION_NAME = 'movies_collection'
MONGO_USERNAME = 'user' # MongoDB username
MONGO_PASSWORD = 'pass' # MongoDB password
MONGO_AUTH_SOURCE = 'admin' # Authentication database for MongoDB

# --- Configuration for Cassandra ---
CASSANDRA_HOSTS = ['localhost'] # Your Cassandra host IP/name
CASSANDRA_PORT = 9042           # Your Cassandra host port
CASSANDRA_KEYSPACE = 'watch_history_db'
CASSANDRA_TABLE = 'watch_history'

# --- (Optional) Cassandra Authentication ---
# If your Cassandra has authentication enabled (not default in basic setup), uncomment and fill these:
# CASSANDRA_USERNAME = 'your_cassandra_username'
# CASSANDRA_PASSWORD = 'your_cassandra_password'


# --- 1. Establish Database Connections ---
mongo_client = None
cassandra_cluster = None
cassandra_session = None

try:
    # Connect to MongoDB
    mongo_client = MongoClient(MONGO_HOST, MONGO_PORT, 
                               username=MONGO_USERNAME, password=MONGO_PASSWORD, 
                               authSource=MONGO_AUTH_SOURCE)
    mongo_db = mongo_client[MONGO_DB_NAME]
    mongo_movies_collection = mongo_db[MONGO_COLLECTION_NAME]
    print(f"Connected to MongoDB: {MONGO_HOST}:{MONGO_PORT}/{MONGO_DB_NAME}")

    # Connect to Cassandra
    # If using authentication, uncomment and use auth_provider:
    # auth_provider = PlainTextAuthProvider(username=CASSANDRA_USERNAME, password=CASSANDRA_PASSWORD)
    # cassandra_cluster = Cluster(CASSANDRA_HOSTS, port=CASSANDRA_PORT, auth_provider=auth_provider)
    
    cassandra_cluster = Cluster(CASSANDRA_HOSTS, port=CASSANDRA_PORT) # For basic setup without auth
    cassandra_session = cassandra_cluster.connect(CASSANDRA_KEYSPACE)
    print(f"Connected to Cassandra: {CASSANDRA_HOSTS}:{CASSANDRA_PORT}/{CASSANDRA_KEYSPACE}")

    # --- 2. Load Movie Genre Data from MongoDB (for Question 3) ---
    print("\nLoading movie genres from MongoDB...")
    movie_genres_lookup = {}
    # Retrieve all movies, selecting only 'movieId' and 'genres'
    # Note: 'movieId' in MongoDB is an int, but 'movie_id' in Cassandra is text.
    # We will store MongoDB's movieId as string keys for easier lookup against Cassandra's movie_id (text).
    for movie in mongo_movies_collection.find({}, {'movieId': 1, 'genres': 1, '_id': 0}):
        movie_id_str = str(movie.get('movieId')) # Convert int to string for consistent lookup
        genres_str = movie.get('genres', '')
        # Split genres string into a list (e.g., "Action|Comedy" -> ["Action", "Comedy"])
        movie_genres_lookup[movie_id_str] = [g.strip() for g in genres_str.split('|') if g.strip()]
    print(f"Loaded {len(movie_genres_lookup)} movie entries from MongoDB.")


    # --- 3. Query Watch History Data from Cassandra ---
    print("\nQuerying watch history from Cassandra...")
    watch_history_records = []
    # Select all necessary columns from watch_history table
    rows = cassandra_session.execute(f"SELECT user_id, movie_id, watch_time, duration_watched FROM {CASSANDRA_TABLE}")
    for row in rows:
        watch_history_records.append(row)
    print(f"Retrieved {len(watch_history_records)} watch history records from Cassandra.")


    # --- 4. Process Queries (Overall Statistics) ---

    # --- Query 1: Banyaknya film yang ditonton setiap hari (Overall) ---
    print("\n--- 1. Jumlah film ditonton setiap hari (Keseluruhan Pengguna) ---")
    overall_movies_watched_daily = Counter()
    for record in watch_history_records:
        watch_date = record.watch_time.strftime('%Y-%m-%d')
        overall_movies_watched_daily[watch_date] += 1
    
    for date, count in sorted(overall_movies_watched_daily.items()):
        print(f"Tanggal {date}: {count} film ditonton")


    # --- Query 2: Waktu user biasa menonton film (Overall) ---
    print("\n--- 2. Waktu user biasa menonton film (berdasarkan jam, Keseluruhan Pengguna) ---")
    overall_watch_time_of_day_counts = Counter()
    for record in watch_history_records:
        watch_hour = record.watch_time.hour
        overall_watch_time_of_day_counts[watch_hour] += 1
    
    for hour, count in sorted(overall_watch_time_of_day_counts.items()):
        print(f"Jam {hour:02d}:00 - {hour:02d}:59: {count} film ditonton")


    # --- Query 3: Genre film apa saja yang biasa ditonton user, dan berdasarkan waktunya apakah ada genre favorit yang ditonton di waktu tertentu (Overall) ---
    print("\n--- 3. Genre film yang biasa ditonton dan genre favorit per waktu (Keseluruhan Pengguna) ---")
    
    overall_genre_counts = Counter() # {genre: count}
    overall_genre_time_counts = defaultdict(Counter) # {hour: {genre: count}}

    for record in watch_history_records:
        movie_id_str = record.movie_id
        watch_hour = record.watch_time.hour

        genres = movie_genres_lookup.get(movie_id_str, [])
        
        for genre in genres:
            overall_genre_counts[genre] += 1
            overall_genre_time_counts[watch_hour][genre] += 1

    print("\n--- Top 10 Genre Favorit Keseluruhan Pengguna ---")
    if overall_genre_counts:
        for genre, count in overall_genre_counts.most_common(10):
            print(f"  '{genre}': {count} tontonan")
    else:
        print("Tidak ada data genre untuk keseluruhan pengguna.")

    print("\n--- Top 5 Genre Favorit Per Waktu (Jam) Keseluruhan Pengguna ---")
    for hour, genres_counter in sorted(overall_genre_time_counts.items()):
        if genres_counter:
            print(f"\n  Jam {hour:02d}:00:")
            for genre, count in genres_counter.most_common(5): # Top 5 per hour
                print(f"    '{genre}': {count} tontonan")
        else:
            print(f"\n  Jam {hour:02d}:00: Tidak ada data genre untuk jam ini.")

except Exception as e:
    print(f"An error occurred: {e}")

finally:
    # --- Close Database Connections ---
    if mongo_client:
        mongo_client.close()
        print("\nMongoDB connection closed.")
    if cassandra_cluster:
        cassandra_cluster.shutdown()
        print("Cassandra connection closed.")


Connected to MongoDB: localhost:27017/moviedb_from_python
An error occurred: ('Unable to connect to any servers', {'127.0.0.1:9042': ConnectionRefusedError(10061, "Tried connecting to [('127.0.0.1', 9042)]. Last error: No connection could be made because the target machine actively refused it"), '::1:9042': ConnectionRefusedError(10061, "Tried connecting to [('::1', 9042, 0, 0)]. Last error: No connection could be made because the target machine actively refused it")})

MongoDB connection closed.
Cassandra connection closed.


# Install cassandra-driver, pymango, kanvas

In [10]:
pip install cassandra-driver

   ---------------------------------------- 0.0/348.6 kB ? eta -:--:--
   - -------------------------------------- 10.2/348.6 kB ? eta -:--:--
   ------------ --------------------------- 112.6/348.6 kB 1.3 MB/s eta 0:00:01
   ------------------------------------- -- 327.7/348.6 kB 2.5 MB/s eta 0:00:01
   ---------------------------------------- 348.6/348.6 kB 2.7 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.0 -> 25.1.1
[notice] To update, run: C:\Users\Kids1\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


In [ ]:

import json
from pymongo import MongoClient
from cassandra.cluster import Cluster
from cassandra.auth import PlainTextAuthProvider # Uncomment if Cassandra auth is enabled
from datetime import datetime
from collections import defaultdict, Counter

# --- Configuration for MongoDB ---
MONGO_HOST = 'localhost'
MONGO_PORT = 27018 # Your MongoDB host port
MONGO_DB_NAME = 'moviedb_from_python'
MONGO_COLLECTION_NAME = 'movies_collection'
MONGO_USERNAME = 'user' # MongoDB username
MONGO_PASSWORD = 'pass' # MongoDB password
MONGO_AUTH_SOURCE = 'admin' # Authentication database for MongoDB

# --- Configuration for Cassandra ---
CASSANDRA_HOSTS = ['localhost'] # Your Cassandra host IP/name
CASSANDRA_PORT = 9042           # Your Cassandra host port
CASSANDRA_KEYSPACE = 'watch_history_db'
CASSANDRA_TABLE = 'watch_history'

# --- (Optional) Cassandra Authentication ---
# If your Cassandra has authentication enabled (not default in basic setup), uncomment and fill these:
# CASSANDRA_USERNAME = 'your_cassandra_username'
# CASSANDRA_PASSWORD = 'your_cassandra_password'


# --- 1. Establish Database Connections ---
mongo_client = None
cassandra_cluster = None
cassandra_session = None

try:
    # Connect to MongoDB
    mongo_client = MongoClient(MONGO_HOST, MONGO_PORT, 
                               username=MONGO_USERNAME, password=MONGO_PASSWORD, 
                               authSource=MONGO_AUTH_SOURCE)
    mongo_db = mongo_client[MONGO_DB_NAME]
    mongo_movies_collection = mongo_db[MONGO_COLLECTION_NAME]
    print(f"Connected to MongoDB: {MONGO_HOST}:{MONGO_PORT}/{MONGO_DB_NAME}")

    # Connect to Cassandra
    # If using authentication, uncomment and use auth_provider:
    # auth_provider = PlainTextAuthProvider(username=CASSANDRA_USERNAME, password=CASSANDRA_PASSWORD)
    # cassandra_cluster = Cluster(CASSANDRA_HOSTS, port=CASSANDRA_PORT, auth_provider=auth_provider)
    
    cassandra_cluster = Cluster(CASSANDRA_HOSTS, port=CASSANDRA_PORT) # For basic setup without auth
    cassandra_session = cassandra_cluster.connect(CASSANDRA_KEYSPACE)
    print(f"Connected to Cassandra: {CASSANDRA_HOSTS}:{CASSANDRA_PORT}/{CASSANDRA_KEYSPACE}")

    # --- 2. Load Movie Genre Data from MongoDB (for Question 3) ---
    print("\nLoading movie genres from MongoDB...")
    movie_genres_lookup = {}
    # Retrieve all movies, selecting only 'movieId' and 'genres'
    # Note: 'movieId' in MongoDB is an int, but 'movie_id' in Cassandra is text.
    # We will store MongoDB's movieId as string keys for easier lookup against Cassandra's movie_id (text).
    for movie in mongo_movies_collection.find({}, {'movieId': 1, 'genres': 1, '_id': 0}):
        movie_id_str = str(movie.get('movieId')) # Convert int to string for consistent lookup
        genres_str = movie.get('genres', '')
        # Split genres string into a list (e.g., "Action|Comedy" -> ["Action", "Comedy"])
        movie_genres_lookup[movie_id_str] = [g.strip() for g in genres_str.split('|') if g.strip()]
    print(f"Loaded {len(movie_genres_lookup)} movie entries from MongoDB.")


    # --- 3. Query Watch History Data from Cassandra ---
    print("\nQuerying watch history from Cassandra...")
    watch_history_records = []
    # Select all necessary columns from watch_history table
    rows = cassandra_session.execute(f"SELECT user_id, movie_id, watch_time, duration_watched FROM {CASSANDRA_TABLE}")
    for row in rows:
        watch_history_records.append(row)
    print(f"Retrieved {len(watch_history_records)} watch history records from Cassandra.")


    # --- 4. Process Queries (Overall Statistics) ---

    # --- Query 1: Banyaknya film yang ditonton setiap hari (Overall) ---
    print("\n--- 1. Jumlah film ditonton setiap hari (Keseluruhan Pengguna) ---")
    overall_movies_watched_daily = Counter()
    for record in watch_history_records:
        watch_date = record.watch_time.strftime('%Y-%m-%d')
        overall_movies_watched_daily[watch_date] += 1
    
    for date, count in sorted(overall_movies_watched_daily.items()):
        print(f"Tanggal {date}: {count} film ditonton")


    # --- Query 2: Waktu user biasa menonton film (Overall) ---
    print("\n--- 2. Waktu user biasa menonton film (berdasarkan jam, Keseluruhan Pengguna) ---")
    overall_watch_time_of_day_counts = Counter()
    for record in watch_history_records:
        watch_hour = record.watch_time.hour
        overall_watch_time_of_day_counts[watch_hour] += 1
    
    for hour, count in sorted(overall_watch_time_of_day_counts.items()):
        print(f"Jam {hour:02d}:00 - {hour:02d}:59: {count} film ditonton")


    # --- Query 3: Genre film apa saja yang biasa ditonton user, dan berdasarkan waktunya apakah ada genre favorit yang ditonton di waktu tertentu (Overall) ---
    print("\n--- 3. Genre film yang biasa ditonton dan genre favorit per waktu (Keseluruhan Pengguna) ---")
    
    overall_genre_counts = Counter() # {genre: count}
    overall_genre_time_counts = defaultdict(Counter) # {hour: {genre: count}}

    for record in watch_history_records:
        movie_id_str = record.movie_id
        watch_hour = record.watch_time.hour

        genres = movie_genres_lookup.get(movie_id_str, [])
        
        for genre in genres:
            overall_genre_counts[genre] += 1
            overall_genre_time_counts[watch_hour][genre] += 1

    print("\n--- Top 10 Genre Favorit Keseluruhan Pengguna ---")
    if overall_genre_counts:
        for genre, count in overall_genre_counts.most_common(10):
            print(f"  '{genre}': {count} tontonan")
    else:
        print("Tidak ada data genre untuk keseluruhan pengguna.")

    print("\n--- Top 5 Genre Favorit Per Waktu (Jam) Keseluruhan Pengguna ---")
    for hour, genres_counter in sorted(overall_genre_time_counts.items()):
        if genres_counter:
            print(f"\n  Jam {hour:02d}:00:")
            for genre, count in genres_counter.most_common(5): # Top 5 per hour
                print(f"    '{genre}': {count} tontonan")
        else:
            print(f"\n  Jam {hour:02d}:00: Tidak ada data genre untuk jam ini.")

except Exception as e:
    print(f"An error occurred: {e}")

finally:
    # --- Close Database Connections ---
    if mongo_client:
        mongo_client.close()
        print("\nMongoDB connection closed.")
    if cassandra_cluster:
        cassandra_cluster.shutdown()
        print("Cassandra connection closed.")


In [2]:
pip install pymongo

   ---------------------------------------- 0.0/848.1 kB ? eta -:--:--
   ---- ----------------------------------- 92.2/848.1 kB 1.7 MB/s eta 0:00:01
   ---------------------- ----------------- 481.3/848.1 kB 5.0 MB/s eta 0:00:01
   ---------------------------------------- 848.1/848.1 kB 6.7 MB/s eta 0:00:00
   ---------------------------------------- 0.0/313.6 kB ? eta -:--:--
   --------------------------------------- 313.6/313.6 kB 19.0 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.0 -> 25.1.1
[notice] To update, run: C:\Users\Kids1\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip
